# Make EQ catalog for pygmm

## Import pygmm module

In [1]:
#import pygmm

In [2]:
import subprocess


## Import ObsPy module
https://anaconda.org/conda-forge/obspy

In [3]:
from obspy import read
from obspy import UTCDateTime
from obspy.clients.fdsn import Client
from obspy.geodetics.base import gps2dist_azimuth

import obspy as ob
print("# obspy version = ",ob.__version__)

# obspy version =  1.2.2


## Import libcomcat module
https://github.com/usgs/libcomcat

In [4]:
# Local imports
from libcomcat.dataframes import get_phase_dataframe, get_magnitude_data_frame
from libcomcat.search import get_event_by_id
from libcomcat.dataframes import (get_detail_data_frame, get_dyfi_data_frame,
                                  get_history_data_frame, get_magnitude_data_frame,
                                  get_pager_data_frame, get_phase_dataframe,
                                  get_summary_data_frame)

## Import SciPy, NumPy, matplotlib module

In [5]:
import numpy as np
import scipy as sp
import matplotlib as mpl
import pandas as pd

print("# numpy version = ",np.__version__)
print("# scipy version = ",sp.__version__)
print("# matplotlib version = ",mpl.__version__)
print("# pandas version = ",pd.__version__)

import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import matplotlib.dates as mdates 


from scipy import signal
from scipy import ndimage

from scipy.fftpack import fft, ifft
from scipy.linalg import norm

from scipy.stats import pearsonr
from scipy.stats import spearmanr
from scipy.stats import kendalltau

import sys
import os


# numpy version =  1.19.1
# scipy version =  1.5.2
# matplotlib version =  3.3.1
# pandas version =  1.0.4


## Font size for plotting

In [6]:
# font size
SMALL_SIZE = 16
MEDIUM_SIZE = 18
BIGGER_SIZE = 20

#SMALL_SIZE = 32
#MEDIUM_SIZE = 32
#BIGGER_SIZE = 36

plt.rc('font', size=SMALL_SIZE)          # controls default text sizes
plt.rc('axes', titlesize=SMALL_SIZE)     # fontsize of the axes title
plt.rc('axes', labelsize=MEDIUM_SIZE)    # fontsize of the x and y labels
plt.rc('xtick', labelsize=SMALL_SIZE)    # fontsize of the tick labels
plt.rc('ytick', labelsize=SMALL_SIZE)    # fontsize of the tick labels
plt.rc('legend', fontsize=SMALL_SIZE)    # legend fontsize
plt.rc('figure', titlesize=BIGGER_SIZE)  # fontsize of the figure title

In [7]:
def event_info(eventid):
    clientEQ = Client("USGS")
    catalog = clientEQ.get_events(eventid=eventid)
    event = catalog[0]
    origin = event.origins[0]
    #origin_time = origin.time
    evla = origin.latitude
    evlo = origin.longitude
    evdp_km = origin.depth / 1000
    evmag = event.magnitudes[0].mag

    print("# evla = ", evla)
    print("# evlo = ", evlo)
    print("# evmag = ", evmag)
    
    return evla, evlo, evmag
    

## Extract focal mechanism information

In [74]:
def focal_info(eventid):
    #eq_detail = get_event_by_id(eventid, includesuperseded=True)
    try:
        eq_detail = get_event_by_id(eventid)
        
        print("Included products: %s " % eq_detail.products)
        try:
            print("# try MT")
            product = eq_detail.getProducts('moment-tensor')[0]
            focal_source = "MT"
            # this way, we may lose MT solution with moment tensor element only...
            dip = product['nodal-plane-1-dip']
            rake = product['nodal-plane-1-rake']
            strike = product['nodal-plane-1-strike']
        except:
            try:
                print("# try FM")
                product = eq_detail.getProducts('focal-mechanism')[0]
                focal_source = "FM"
                dip = product['nodal-plane-1-dip']
                rake = product['nodal-plane-1-rake']
                strike = product['nodal-plane-1-strike']
            except:
                focal_source = "NA"
                dip = -999
                rake = -999
                strike = -999
        #if focal_source == "NA":
        #    dip = -999
        #    rake = -999
        #    strike = -999
        #else:
        #    print("# loop focal_source = ", focal_source)
        #    dip = product['nodal-plane-1-dip']
        #    rake = product['nodal-plane-1-rake']
        #    strike = product['nodal-plane-1-strike']
    except:
        dip = -999
        rake = -999
        strike = -999
        focal_source = "NA2"
        
    print("# strike = ", strike)
    print("# dip = ", dip)
    print("# rake = ", rake)
    print("# focal_source = ", focal_source)
    return strike, dip, rake, focal_source

In [76]:
def focal_info_includesuperseded(eventid):
    #eq_detail = get_event_by_id(eventid, includesuperseded=True)
    try:
        eq_detail = get_event_by_id(eventid, includesuperseded=True)

        print("Included products: %s " % eq_detail.products)
        try:
            print("# try MT")
            product = eq_detail.getProducts('moment-tensor')[0]
            focal_source = "MT"
            # this way, we may lose MT solution with moment tensor element only...
            dip = product['nodal-plane-1-dip']
            rake = product['nodal-plane-1-rake']
            strike = product['nodal-plane-1-strike']
        except:
            try:
                print("# try FM")
                product = eq_detail.getProducts('focal-mechanism')[0]
                focal_source = "FM"
                dip = product['nodal-plane-1-dip']
                rake = product['nodal-plane-1-rake']
                strike = product['nodal-plane-1-strike']
            except:
                focal_source = "NA"
                dip = -999
                rake = -999
                strike = -999
        #if focal_source == "NA":
        #    dip = -999
        #    rake = -999
        #    strike = -999
        #else:
        #    print("# loop focal_source = ", focal_source)
        #    dip = product['nodal-plane-1-dip']
        #    rake = product['nodal-plane-1-rake']
        #    strike = product['nodal-plane-1-strike']
    except:
        dip = -999
        rake = -999
        strike = -999
        focal_source = "NA2"
        
    print("# strike = ", strike)
    print("# dip = ", dip)
    print("# rake = ", rake)
    print("# focal_source = ", focal_source)
    return strike, dip, rake, focal_source

In [56]:
## Compute "mechanism" info

In [161]:
#def mechanism_info(strike, dip, rake):
def mechanism_info(strike, dip, rake, evlo, evla, evdp_km, evmag, eventid, scalarOPT=1):

    ### use FMC.py to get fault-type
    #AR Focal mechanism one plane (psmeca compatible):[longitude, latitude, depth, strike, dip, rake, magnitude (Mw),X plot, Y plot (for GMT), ID, TYPE]
    # these info. are not used to compute rupture info
    #evlo=120.0
    #evla=40.0
    #evdp_km=5.0
    #evmag=3.0
    #eventid="001"
    focal_csv = "focal.csv"
    #focal_df = pd.DataFrame({ 'lon' : evlo})
    print("# evlo", evlo)

    if scalarOPT == 1:
        focal_df = pd.DataFrame({ 'lon' : evlo,
                                'lat' : evla,
                                'dep' : evdp_km,
                                'strike' : strike,
                                'dip' : dip,
                                'rake' : rake,
                                'mag' : evmag,
                                'evid' : eventid }, index=[0])
    else:
        focal_df = pd.DataFrame({ 'lon' : evlo,
                                'lat' : evla,
                                'dep' : evdp_km,
                                'strike' : strike,
                                'dip' : dip,
                                'rake' : rake,
                                'mag' : evmag,
                                'evid' : eventid }  )
    focal_df.to_csv(focal_csv, columns=['lon','lat','dep','strike','dip','rake','mag','lon','lat','evid'], header=False, index=False, sep=' ')

    # inside of run_FMC.sh
    #%%script tcsh
    #./SOFTX_2018_227-master/FMC.py  < ./focal.csv -i AR -o ALL -p focal.csv.png >! focal.csv_fault_type.out
    subprocess.call( ["./run_FMC.sh"] ) 



    fault_type_fi = "focal.csv_fault_type.out"
    fault_type_df = pd.read_csv(fault_type_fi,   
                           sep=" ")
    #print(fpfit_catalog_hypoDD_fault_type )

    #Abbreviation	Name
    #u	Unspecified
    #ss	Strike-slip
    #ns	Normal slip
    #rs	Reverse slip

    fault_type_df ['fault_type']  = -9
    fault_type_df ['mechanism'] = "U"

    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "N")  |  (fault_type_df['Rupture_type'] == "N-SS")  , 'fault_type'] = 0
    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "N")  |  (fault_type_df['Rupture_type'] == "N-SS")  , 'mechanism'] = "NS"

    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "R")  |  (fault_type_df['Rupture_type'] == "R-SS")  , 'fault_type'] = 1
    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "R")  |  (fault_type_df['Rupture_type'] == "R-SS")  , 'mechanism'] = "RS"

    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "SS")  |  (fault_type_df['Rupture_type'] == "SS-N")   |  (fault_type_df['Rupture_type'] == "SS-R")  , 'fault_type'] = 2
    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "SS")  |  (fault_type_df['Rupture_type'] == "SS-N")   |  (fault_type_df['Rupture_type'] == "SS-R")  , 'mechanism'] = "SS"

    # to see if we have -9; if so, this would be a problem
    #fault_type_df[fault_type_df['fault_type']  ==  -9]
    print("# Rupture_type = ", fault_type_df['Rupture_type'])

    #mechanism = fault_type_df['mechanism'][0]
    #print("# mechanism = ", mechanism)
    
    print("# mechanism = ", fault_type_df['mechanism'])
    return fault_type_df['Rupture_type'], fault_type_df['mechanism']

In [179]:
#def mechanism_info(strike, dip, rake):
def mechanism_info_fromCMT(mrr, mtt, mff, mrt, mrf, mtf, evlo, evla, evdp_km, evmag, eventid, scalarOPT=1):

    convert_Nm_dyncm = 10000000
    M0_exponent_Nm = 10E+17
    M0_exponent_dyncm_OUT = 25 # ideally this would get from M0_exponent_dyncm and this is scalar... may need to make array if we do not use scalarOPT

    M0_exponent_dyncm = M0_exponent_Nm * convert_Nm_dyncm
    #print("# M0_exponent_dyncm = ", M0_exponent_dyncm )

    #mrr = float(product['tensor-mrr'])
    #mtt = float(product['tensor-mtt'])
    #mff = float(product['tensor-mpp'])

    #mrt = float(product['tensor-mrt'])
    #mrf = float(product['tensor-mrp'])
    #mtf = float(product['tensor-mtp'])

    
    mrr_dyncm = mrr * convert_Nm_dyncm
    mtt_dyncm = mtt * convert_Nm_dyncm
    mff_dyncm = mff * convert_Nm_dyncm

    mrt_dyncm = mrt * convert_Nm_dyncm
    mrf_dyncm = mrf * convert_Nm_dyncm
    mtf_dyncm = mtf * convert_Nm_dyncm
    mrr_norm_dyncm = mrr_dyncm  / M0_exponent_dyncm
    mtt_norm_dyncm = mtt_dyncm  / M0_exponent_dyncm
    mff_norm_dyncm = mff_dyncm  / M0_exponent_dyncm

    mrt_norm_dyncm = mrt_dyncm  / M0_exponent_dyncm
    mrf_norm_dyncm = mrf_dyncm  / M0_exponent_dyncm
    mtf_norm_dyncm = mtf_dyncm  / M0_exponent_dyncm

    ### use FMC.py to get fault-type
    #AR Focal mechanism one plane (psmeca compatible):[longitude, latitude, depth, strike, dip, rake, magnitude (Mw),X plot, Y plot (for GMT), ID, TYPE]
    # these info. are not used to compute rupture info
    #evlo=120.0
    #evla=40.0
    #evdp_km=5.0
    #evmag=3.0
    #eventid="001"
    focal_CMT_csv = "focal_CMT.csv"
    #focal_df = pd.DataFrame({ 'lon' : evlo})
    print("# evlo", evlo)

    if scalarOPT == 1:
       
        focal_CMT_df = pd.DataFrame({ 'lon' : evlo,
                        'lat' : evla,
                        'dep' : evdp_km,
                        'mrr' : mrr_norm_dyncm,
                        'mtt' : mtt_norm_dyncm,
                        'mff' : mff_norm_dyncm,
                        'mrt' : mrt_norm_dyncm,
                        'mrf' : mrf_norm_dyncm,
                        'mtf' : mtf_norm_dyncm ,
                        'Exponent' :  M0_exponent_dyncm_OUT,
                        'evid' : eventid }, index=[0])

    else:
        focal_CMT_df = pd.DataFrame({ 'lon' : evlo,
                        'lat' : evla,
                        'dep' : evdp_km,
                        'mrr' : mrr_norm_dyncm,
                        'mtt' : mtt_norm_dyncm,
                        'mff' : mff_norm_dyncm,
                        'mrt' : mrt_norm_dyncm,
                        'mrf' : mrf_norm_dyncm,
                        'mtf' : mtf_norm_dyncm ,
                        'Exponent' :  M0_exponent_dyncm_OUT,
                        'evid' : eventid } )         

    #focal_df.to_csv(focal_csv, columns=['lon','lat','dep','strike','dip','rake','mag','lon','lat','evid'], header=False, index=False, sep=' ')
    focal_CMT_df.to_csv(focal_CMT_csv, columns=['lon','lat','dep','mrr','mtt','mff','mrt','mrf','mtf','Exponent','lon','lat','evid'], header=False, index=False, sep=' ')

    # inside of run_FMC.sh
    #%%script tcsh
    #./SOFTX_2018_227-master/FMC.py  < ./focal.csv -i AR -o ALL -p focal.csv.png >! focal.csv_fault_type.out
    subprocess.call( ["./run_FMC_CMT.sh"] ) 



    fault_type_fi = "focal_CMT.csv_fault_type.out"
    fault_type_df = pd.read_csv(fault_type_fi,   
                           sep=" ")
    #print(fpfit_catalog_hypoDD_fault_type )

    #Abbreviation	Name
    #u	Unspecified
    #ss	Strike-slip
    #ns	Normal slip
    #rs	Reverse slip

    fault_type_df ['fault_type']  = -9
    fault_type_df ['mechanism'] = "U"

    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "N")  |  (fault_type_df['Rupture_type'] == "N-SS")  , 'fault_type'] = 0
    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "N")  |  (fault_type_df['Rupture_type'] == "N-SS")  , 'mechanism'] = "NS"

    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "R")  |  (fault_type_df['Rupture_type'] == "R-SS")  , 'fault_type'] = 1
    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "R")  |  (fault_type_df['Rupture_type'] == "R-SS")  , 'mechanism'] = "RS"

    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "SS")  |  (fault_type_df['Rupture_type'] == "SS-N")   |  (fault_type_df['Rupture_type'] == "SS-R")  , 'fault_type'] = 2
    fault_type_df.loc[   (fault_type_df['Rupture_type'] == "SS")  |  (fault_type_df['Rupture_type'] == "SS-N")   |  (fault_type_df['Rupture_type'] == "SS-R")  , 'mechanism'] = "SS"

    # to see if we have -9; if so, this would be a problem
    #fault_type_df[fault_type_df['fault_type']  ==  -9]
    print("# Rupture_type = ", fault_type_df['Rupture_type'])

    #mechanism = fault_type_df['mechanism'][0]
    #print("# mechanism = ", mechanism)
    
    print("# mechanism = ", fault_type_df['mechanism'])
    return fault_type_df['Rupture_type'], fault_type_df['mechanism']

## Read event csv file


In [58]:
event_fi = "bayarea_center_m3_500km.csv"
#event_fi = "test_eq.csv" # two events only

event_df = pd.read_csv(event_fi ,   
                       sep=",")

In [59]:
print(event_df)

                          time   latitude   longitude  depth   mag magType  \
0     2020-12-01T23:47:05.591Z  38.167500 -118.081300   5.60  4.30      ml   
1     2020-12-01T23:43:08.516Z  38.172700 -118.070300   4.80  4.30      ml   
2     2020-12-01T23:39:55.064Z  38.172200 -118.050400   8.00  3.20      ml   
3     2020-12-01T23:35:42.457Z  38.163800 -118.084400   4.70  3.10      ml   
4     2020-12-01T23:32:56.573Z  38.163700 -118.083700   5.00  5.10      ml   
...                        ...        ...         ...    ...   ...     ...   
2127  2018-01-11T00:15:13.680Z  36.156333 -120.229833  11.36  3.14      ml   
2128  2018-01-07T19:01:00.490Z  40.398667 -125.244667  29.45  4.52      mw   
2129  2018-01-07T01:31:11.150Z  34.420000 -120.001500   2.26  3.78      mw   
2130  2018-01-04T10:39:37.730Z  37.855167 -122.256833  12.31  4.38      mw   
2131  2017-12-31T19:49:06.270Z  40.484667 -123.390000  30.44  3.76      mw   

        nst     gap      dmin     rms  ...                   up

In [60]:
event_df['strike'] = event_df['latitude']
event_df['dip'] = event_df['latitude']
event_df['rake'] = event_df['latitude']
event_df['focal_source'] = event_df['magType']
event_df['Rupture_type'] = event_df['magType']
event_df['mechanism'] = event_df['magType']



In [61]:
#for eventid in event_df['id']:
for i, eventid in enumerate(event_df['id']):

    print("# i = ",i)
    print("# evenid = ", eventid)
    #evla, evlo, evmag = event_info(eventid)
    strike, dip, rake, focal_source  = focal_info(eventid)
    #event_df['strike'][i], event_df['dip'][i], event_df['rake'][i], event_df['focal_source'][i]  = focal_info(eventid)

    print("# strile = ", strike)
    print("# dip = ", dip)
    print("# rake = ", rake)
    event_df.loc[i, 'strike'] = strike
    event_df.loc[i, 'dip'] = dip
    event_df.loc[i, 'rake'] = rake
    event_df.loc[i, 'focal_source'] = focal_source

    #mechanism_info(strike, dip, rake)
    

# i =  0
# evenid =  nn00787133
Included products: ['dyfi', 'losspager', 'moment-tensor', 'origin', 'phase-data', 'shakemap'] 
# try MT
# strike =  170.49
# dip =  41.55
# rake =  -134.82
# focal_source =  MT
# strile =  170.49
# dip =  41.55
# rake =  -134.82
# i =  1
# evenid =  nn00787124
Included products: ['losspager', 'moment-tensor', 'origin', 'phase-data', 'shakemap'] 
# try MT
# strike =  83.27
# dip =  80.06
# rake =  -16.7
# focal_source =  MT
# strile =  83.27
# dip =  80.06
# rake =  -16.7
# i =  2
# evenid =  nn00787116
# strike =  -999
# dip =  -999
# rake =  -999
# focal_source =  NA2
# strile =  -999
# dip =  -999
# rake =  -999
# i =  3
# evenid =  nn00787110
Included products: ['origin', 'phase-data'] 
# try MT
# try FM
# strike =  -999
# dip =  -999
# rake =  -999
# focal_source =  NA
# strile =  -999
# dip =  -999
# rake =  -999
# i =  4
# evenid =  nn00787105
Included products: ['dyfi', 'ground-failure', 'losspager', 'moment-tensor', 'origin', 'phase-data', 'shake

In [62]:
#eq_detail = get_event_by_id("nn00787116")


In [63]:
#strike, dip, rake, focal_source  = focal_info("nn00787116")


In [64]:
event_df['strike']

0       170.49
1        83.27
2         -999
3         -999
4       168.57
         ...  
2127     105.0
2128      -999
2129     167.0
2130      60.0
2131      75.0
Name: strike, Length: 2132, dtype: object

In [65]:
event_df['longitude']

0      -118.081300
1      -118.070300
2      -118.050400
3      -118.084400
4      -118.083700
           ...    
2127   -120.229833
2128   -125.244667
2129   -120.001500
2130   -122.256833
2131   -123.390000
Name: longitude, Length: 2132, dtype: float64

In [66]:
#event_df.loc[0, 'strike'] = 300
#event_df.loc[1, 'strike'] = 200

#event_df.loc[0, 'dip'] = 30 
#event_df.loc[1, 'dip'] = 90

#event_df.loc[0, 'rake'] = 0
#event_df.loc[1, 'rake'] = 180


In [67]:
#mechanism_info(event_df['strike'],  event_df['dip'], event_df['rake'])
#mechanism_info(strike, dip, rake, evlo, evla, evdp_km, evmag, evid
#                 depth  maglongitude
event_df['Rupture_type'] , event_df['mechanism'] = mechanism_info(event_df['strike'],  event_df['dip'], event_df['rake'], event_df['longitude'], event_df['latitude'],  event_df['depth'],  event_df['mag'],  event_df['id'])


# evlo 0      -118.081300
1      -118.070300
2      -118.050400
3      -118.084400
4      -118.083700
           ...    
2127   -120.229833
2128   -125.244667
2129   -120.001500
2130   -122.256833
2131   -123.390000
Name: longitude, Length: 2132, dtype: float64
# Rupture_type =  0       N-SS
1         SS
2          R
3          R
4       SS-N
        ... 
2127       R
2128       R
2129    SS-N
2130    SS-N
2131       N
Name: Rupture_type, Length: 2132, dtype: object
# mechanism =  0       NS
1       SS
2       RS
3       RS
4       SS
        ..
2127    RS
2128    RS
2129    SS
2130    SS
2131    NS
Name: mechanism, Length: 2132, dtype: object


In [68]:
print(event_df['Rupture_type'])

0       N-SS
1         SS
2          R
3          R
4       SS-N
        ... 
2127       R
2128       R
2129    SS-N
2130    SS-N
2131       N
Name: Rupture_type, Length: 2132, dtype: object


In [69]:
print(event_df['mechanism'])

0       NS
1       SS
2       RS
3       RS
4       SS
        ..
2127    RS
2128    RS
2129    SS
2130    SS
2131    NS
Name: mechanism, Length: 2132, dtype: object


In [72]:
event_df.loc[   (event_df['focal_source'] == "NA")  |  (event_df['focal_source'] == "NA2")   , 'mechanism'] = 'U'
event_df.loc[   (event_df['focal_source'] == "NA")  |  (event_df['focal_source'] == "NA2")   , 'Rupture_type'] = 'U'


### recheck MT  with CMT solution only

In [ ]:
"NA2" can check if focal_info_includesuperseded(eventid)

In [113]:
event_NA2_df = event_df[event_df['focal_source']  == "NA2"]
print(event_NA2_df)

                        time   latitude   longitude  depth   mag magType  \
2   2020-12-01T23:39:55.064Z  38.172200 -118.050400   8.00  3.20      ml   
15  2020-11-22T01:35:02.172Z  38.175900 -117.889500  10.50  3.80      ml   
16  2020-11-20T10:10:05.966Z  38.174600 -117.801500   7.40  4.00      ml   
17  2020-11-19T18:22:23.790Z  35.081000 -118.826833   2.71  3.06      ml   
18  2020-11-16T13:52:23.067Z  38.187300 -117.750700  10.80  3.20      ml   
20  2020-11-16T04:43:08.432Z  38.189400 -117.748200  10.60  3.60      ml   
22  2020-11-14T15:07:33.127Z  38.184900 -117.750500  10.70  3.00      ml   
23  2020-11-14T12:42:37.140Z  38.162600 -117.867300   5.20  3.40      ml   
30  2020-11-13T11:32:48.171Z  38.189400 -117.753600  10.50  3.10      ml   
41  2020-11-04T00:20:24.770Z  37.639167 -119.389833  11.81  3.40      ml   
47  2020-10-27T05:45:59.765Z  38.183300 -117.867700   9.90  3.10      ml   

     nst    gap     dmin     rms  ... magNst    status locationSource  \
2   28.0  42.5

In [114]:
event_NA2_df['id'].index

Int64Index([2, 15, 16, 17, 18, 20, 22, 23, 30, 41, 47], dtype='int64')

In [115]:
event_NA2_df['id'].index

Int64Index([2, 15, 16, 17, 18, 20, 22, 23, 30, 41, 47], dtype='int64')

                          time   latitude   longitude  depth   mag magType  \
3     2020-12-01T23:35:42.457Z  38.163800 -118.084400   4.70  3.10      ml   
5     2020-12-01T23:10:47.074Z  39.472400 -119.370800  13.10  3.80      ml   
8     2020-11-30T11:51:23.914Z  38.149700 -117.988800  10.60  3.00      ml   
9     2020-11-30T10:25:26.573Z  38.072600 -118.260700   8.00  3.00      ml   
11    2020-11-29T15:46:52.440Z  40.279000 -124.413667  20.23  3.53      mw   
...                        ...        ...         ...    ...   ...     ...   
2101  2018-03-09T06:01:28.350Z  40.291833 -124.542333  15.09  4.48      mw   
2116  2018-02-03T03:12:46.560Z  40.801000 -125.445500  13.29  4.33      mw   
2119  2018-01-27T12:40:13.570Z  40.380900 -126.311500  10.00  3.30      ml   
2120  2018-01-25T18:26:50.680Z  40.382400 -126.470000  10.74  3.30      ml   
2128  2018-01-07T19:01:00.490Z  40.398667 -125.244667  29.45  4.52      mw   

       nst     gap     dmin     rms  ... magNst    status locat

Int64Index([   3,    5,    8,    9,   11,   13,   14,   21,   25,   26,
            ...
            2078, 2081, 2082, 2091, 2097, 2101, 2116, 2119, 2120, 2128],
           dtype='int64', length=1316)

In [125]:
#for eventid in event_df['id']:
for i, index in enumerate(event_NA2_df['id'].index):
#for i, index in enumerate(event_NA_df['id'].index):

    print("# i = ",i)
    print("# index = ", index)
    eventid=event_NA2_df['id'][index]
    #eventid=event_NA_df['id'][index]

    print("# eventid = ", eventid)

    returnOPT = 0
    MTOPT = 0
    mechOPT = 0
    CMTOPT = 0
    dip = -999
    rake = -999
    strike = -999
    mrr = -999
    mtt = -999
    mff = -999
    mrt = -999
    mrf = -999
    mtf = -999

    FMOPT = 0
    mechOPT_fm = 0
    dip_fm = -999
    rake_fm = -999
    strike_fm = -999

    try:
        eq_detail = get_event_by_id(eventid, includesuperseded=True)
        returnOPT = 1
    except:
        returnOPT = 0
        
    if returnOPT == 1:
        print("Included products: %s " % eq_detail.products)

        MTOPT = 0
        try:
            mt_product = eq_detail.getProducts('moment-tensor')[0]
            print(mt_product)
            MTOPT = 1
        except:
            MTOPT = 0
        
        FMOPT = 0
        try:
            fm_product = eq_detail.getProducts('focal-mechanism')[0]
            print(fm_product)
            FMOPT = 1
        except:
            FMOPT = 0
        
        if FMOPT == 1:
            mechOPT_fm = 0 
            try:
                dip_fm = fm_product['nodal-plane-1-dip']
                rake_fm = fm_product['nodal-plane-1-rake']
                strike_fm = fm_product['nodal-plane-1-strike']
                mechOPT_fm = 1
            except:
                mechOPT_fm = 0
                dip_fm = -999
                rake_fm = -999
                strike_fm = -999
                
        if MTOPT == 1:
            mechOPT = 0
            try:
                dip = mt_product['nodal-plane-1-dip']
                rake = mt_product['nodal-plane-1-rake']
                strike = mt_product['nodal-plane-1-strike']
                mechOPT = 1
            except:
                mechOPT = 0
                dip = -999
                rake = -999
                strike = -999
                
            CMTOPT = 0
            try:
                mrr = float(mt_product['tensor-mrr'])
                mtt = float(mt_product['tensor-mtt'])
                mff = float(mt_product['tensor-mpp'])

                mrt = float(mt_product['tensor-mrt'])
                mrf = float(mt_product['tensor-mrp'])
                mtf = float(mt_product['tensor-mtp'])
                CMTOPT = 1
            except:
                mrr = -999
                mtt = -999
                mff = -999
                mrt = -999
                mrf = -999
                mtf = -999
                CMTOPT = 0
     
    print("# returnOPT = ", returnOPT)

        
    print("# FMOPT = ", FMOPT)
    print("# mechOPT_fm = ", mechOPT_fm)
    print("# strike_fm = ", strike_fm)
    print("# dip_fm = ", dip_fm)
    print("# rake_fm = ", rake_fm)
    
    print("# MTOPT = ", MTOPT)
    print("# mechOPT = ", mechOPT)
    print("# strike = ", strike)
    print("# dip = ", dip)
    print("# rake = ", rake)
    print("# CMTOPT = ", CMTOPT)

    # MT is MT-mech strike, dip, rake
    # CMT is CMT CMT moment tensor elements
    # FM is focal mech, strike, dip, rake

    # MT would be better but if we have FM then stick with FM now
    # we only do additional step if we only have CMT 
    focal_source = "NA3"

    if mechOPT == 1:
        focal_source = "MT"
        event_NA2_df.loc[index, 'strike'] = strike
        event_NA2_df.loc[index, 'dip'] = dip
        event_NA2_df.loc[index, 'rake'] = rake
    else:
        if CMTOPT == 1:
            focal_source = "CMT"
    # if mechOPT_fm then we overwrite focal_source
    if mechOPT_fm == 1:
        focal_source = "FM"
        event_NA2_df.loc[index, 'strike'] = strike_fm
        event_NA2_df.loc[index, 'dip'] = dip_fm
        event_NA2_df.loc[index, 'rake'] = rake_fm
    print("# focal_source = ", focal_source )
    #strike, dip, rake, focal_source  = focal_info_includesuperseded(eventid)
    #event_df['strike'][i], event_df['dip'][i], event_df['rake'][i], event_df['focal_source'][i]  = focal_info(eventid)

    #print("# strile = ", strike)
    #print("# dip = ", dip)
    #print("# rake = ", rake)

    event_NA2_df.loc[index, 'focal_source'] = focal_source
    

# i =  0
# index =  2
# eventid =  nn00787116
Included products: ['dyfi', 'origin', 'phase-data', 'shakemap'] 
# returnOPT =  1
# FMOPT =  0
# mechOPT_fm =  0
# strike_fm =  -999
# dip_fm =  -999
# rake_fm =  -999
# MTOPT =  0
# mechOPT =  0
# strike =  -999
# dip =  -999
# rake =  -999
# CMTOPT =  0
# focal_source =  NA3
# i =  1
# index =  15
# eventid =  nn00785639


/Users/taira/opt/anaconda3/envs/pygmm/lib/python3.8/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


Included products: ['dyfi', 'origin', 'phase-data', 'shakemap'] 
# returnOPT =  1
# FMOPT =  0
# mechOPT_fm =  0
# strike_fm =  -999
# dip_fm =  -999
# rake_fm =  -999
# MTOPT =  0
# mechOPT =  0
# strike =  -999
# dip =  -999
# rake =  -999
# CMTOPT =  0
# focal_source =  NA3
# i =  2
# index =  16
# eventid =  nn00785349
Included products: ['dyfi', 'losspager', 'moment-tensor', 'origin', 'phase-data', 'shakemap'] 
Product moment-tensor from us updated 2020-12-21 14:36:24.040000 containing 2 content files.
# returnOPT =  1
# FMOPT =  0
# mechOPT_fm =  0
# strike_fm =  -999
# dip_fm =  -999
# rake_fm =  -999
# MTOPT =  1
# mechOPT =  1
# strike =  174.39
# dip =  57.76
# rake =  171.68
# CMTOPT =  1
# focal_source =  MT
# i =  3
# index =  17
# eventid =  ci39470639
Included products: ['dyfi', 'focal-mechanism', 'nearby-cities', 'origin', 'phase-data', 'scitech-link'] 
Product focal-mechanism from ci updated 2020-11-19 19:25:36.550000 containing 4 content files.
# returnOPT =  1
# FMOP

In [120]:
print(event_NA2_df)

                        time   latitude   longitude  depth   mag magType  \
2   2020-12-01T23:39:55.064Z  38.172200 -118.050400   8.00  3.20      ml   
15  2020-11-22T01:35:02.172Z  38.175900 -117.889500  10.50  3.80      ml   
16  2020-11-20T10:10:05.966Z  38.174600 -117.801500   7.40  4.00      ml   
17  2020-11-19T18:22:23.790Z  35.081000 -118.826833   2.71  3.06      ml   
18  2020-11-16T13:52:23.067Z  38.187300 -117.750700  10.80  3.20      ml   
20  2020-11-16T04:43:08.432Z  38.189400 -117.748200  10.60  3.60      ml   
22  2020-11-14T15:07:33.127Z  38.184900 -117.750500  10.70  3.00      ml   
23  2020-11-14T12:42:37.140Z  38.162600 -117.867300   5.20  3.40      ml   
30  2020-11-13T11:32:48.171Z  38.189400 -117.753600  10.50  3.10      ml   
41  2020-11-04T00:20:24.770Z  37.639167 -119.389833  11.81  3.40      ml   
47  2020-10-27T05:45:59.765Z  38.183300 -117.867700   9.90  3.10      ml   

     nst    gap     dmin     rms  ... magNst    status locationSource  \
2   28.0  42.5

In [124]:
event_NA_df = event_df[event_df['focal_source']  == "NA"]
print(event_NA_df)

                          time   latitude   longitude  depth   mag magType  \
3     2020-12-01T23:35:42.457Z  38.163800 -118.084400   4.70  3.10      ml   
5     2020-12-01T23:10:47.074Z  39.472400 -119.370800  13.10  3.80      ml   
8     2020-11-30T11:51:23.914Z  38.149700 -117.988800  10.60  3.00      ml   
9     2020-11-30T10:25:26.573Z  38.072600 -118.260700   8.00  3.00      ml   
11    2020-11-29T15:46:52.440Z  40.279000 -124.413667  20.23  3.53      mw   
...                        ...        ...         ...    ...   ...     ...   
2101  2018-03-09T06:01:28.350Z  40.291833 -124.542333  15.09  4.48      mw   
2116  2018-02-03T03:12:46.560Z  40.801000 -125.445500  13.29  4.33      mw   
2119  2018-01-27T12:40:13.570Z  40.380900 -126.311500  10.00  3.30      ml   
2120  2018-01-25T18:26:50.680Z  40.382400 -126.470000  10.74  3.30      ml   
2128  2018-01-07T19:01:00.490Z  40.398667 -125.244667  29.45  4.52      mw   

       nst     gap     dmin     rms  ... magNst    status locat

In [126]:
event_NA_df['id'].index

Int64Index([   3,    5,    8,    9,   11,   13,   14,   21,   25,   26,
            ...
            2078, 2081, 2082, 2091, 2097, 2101, 2116, 2119, 2120, 2128],
           dtype='int64', length=1316)

 mrr = -999
                mtt = -999
                mff = -999
                mrt = -999
                mrf = -999
                mtf = -999

In [129]:
event_NA_df['mrr'] = event_NA_df['strike'] 
event_NA_df['mtt'] = event_NA_df['strike'] 
event_NA_df['mff'] = event_NA_df['strike'] 
event_NA_df['mrt'] = event_NA_df['strike'] 
event_NA_df['mrf'] = event_NA_df['strike'] 
event_NA_df['mtf'] = event_NA_df['strike'] 
print(event_NA_df)


                          time   latitude   longitude  depth   mag magType  \
3     2020-12-01T23:35:42.457Z  38.163800 -118.084400   4.70  3.10      ml   
5     2020-12-01T23:10:47.074Z  39.472400 -119.370800  13.10  3.80      ml   
8     2020-11-30T11:51:23.914Z  38.149700 -117.988800  10.60  3.00      ml   
9     2020-11-30T10:25:26.573Z  38.072600 -118.260700   8.00  3.00      ml   
11    2020-11-29T15:46:52.440Z  40.279000 -124.413667  20.23  3.53      mw   
...                        ...        ...         ...    ...   ...     ...   
2101  2018-03-09T06:01:28.350Z  40.291833 -124.542333  15.09  4.48      mw   
2116  2018-02-03T03:12:46.560Z  40.801000 -125.445500  13.29  4.33      mw   
2119  2018-01-27T12:40:13.570Z  40.380900 -126.311500  10.00  3.30      ml   
2120  2018-01-25T18:26:50.680Z  40.382400 -126.470000  10.74  3.30      ml   
2128  2018-01-07T19:01:00.490Z  40.398667 -125.244667  29.45  4.52      mw   

       nst     gap     dmin     rms  ...  rake focal_source Rup

<ipython-input-129-636b579fc570>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  event_NA_df['mrr'] = event_NA_df['strike']
<ipython-input-129-636b579fc570>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  event_NA_df['mtt'] = event_NA_df['strike']
<ipython-input-129-636b579fc570>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/s

In [130]:
#for eventid in event_df['id']:
#for i, index in enumerate(event_NA2_df['id'].index):
for i, index in enumerate(event_NA_df['id'].index):

    print("# i = ",i)
    print("# index = ", index)
    #eventid=event_NA2_df['id'][index]
    eventid=event_NA_df['id'][index]

    print("# eventid = ", eventid)

    returnOPT = 0
    MTOPT = 0
    mechOPT = 0
    CMTOPT = 0
    dip = -999
    rake = -999
    strike = -999
    mrr = -999
    mtt = -999
    mff = -999
    mrt = -999
    mrf = -999
    mtf = -999

    FMOPT = 0
    mechOPT_fm = 0
    dip_fm = -999
    rake_fm = -999
    strike_fm = -999

    try:
        eq_detail = get_event_by_id(eventid, includesuperseded=True)
        returnOPT = 1
    except:
        returnOPT = 0
        
    if returnOPT == 1:
        print("Included products: %s " % eq_detail.products)

        MTOPT = 0
        try:
            mt_product = eq_detail.getProducts('moment-tensor')[0]
            print(mt_product)
            MTOPT = 1
        except:
            MTOPT = 0
        
        FMOPT = 0
        try:
            fm_product = eq_detail.getProducts('focal-mechanism')[0]
            print(fm_product)
            FMOPT = 1
        except:
            FMOPT = 0
        
        if FMOPT == 1:
            mechOPT_fm = 0 
            try:
                dip_fm = fm_product['nodal-plane-1-dip']
                rake_fm = fm_product['nodal-plane-1-rake']
                strike_fm = fm_product['nodal-plane-1-strike']
                mechOPT_fm = 1
            except:
                mechOPT_fm = 0
                dip_fm = -999
                rake_fm = -999
                strike_fm = -999
                
        if MTOPT == 1:
            mechOPT = 0
            try:
                dip = mt_product['nodal-plane-1-dip']
                rake = mt_product['nodal-plane-1-rake']
                strike = mt_product['nodal-plane-1-strike']
                mechOPT = 1
            except:
                mechOPT = 0
                dip = -999
                rake = -999
                strike = -999
                
            CMTOPT = 0
            try:
                mrr = float(mt_product['tensor-mrr'])
                mtt = float(mt_product['tensor-mtt'])
                mff = float(mt_product['tensor-mpp'])

                mrt = float(mt_product['tensor-mrt'])
                mrf = float(mt_product['tensor-mrp'])
                mtf = float(mt_product['tensor-mtp'])
                CMTOPT = 1
            except:
                mrr = -999
                mtt = -999
                mff = -999
                mrt = -999
                mrf = -999
                mtf = -999
                CMTOPT = 0
     
    print("# returnOPT = ", returnOPT)

        
    print("# FMOPT = ", FMOPT)
    print("# mechOPT_fm = ", mechOPT_fm)
    print("# strike_fm = ", strike_fm)
    print("# dip_fm = ", dip_fm)
    print("# rake_fm = ", rake_fm)
    
    print("# MTOPT = ", MTOPT)
    print("# mechOPT = ", mechOPT)
    print("# strike = ", strike)
    print("# dip = ", dip)
    print("# rake = ", rake)
    print("# CMTOPT = ", CMTOPT)

    # MT is MT-mech strike, dip, rake
    # CMT is CMT CMT moment tensor elements
    # FM is focal mech, strike, dip, rake

    # MT would be better but if we have FM then stick with FM now
    # we only do additional step if we only have CMT 
    focal_source = "NA3"

    if mechOPT == 1:
        focal_source = "MT"
        event_NA_df.loc[index, 'strike'] = strike
        event_NA_df.loc[index, 'dip'] = dip
        event_NA_df.loc[index, 'rake'] = rake
    else:
        if CMTOPT == 1:
            focal_source = "CMT"
            event_NA_df.loc[index, 'mrr'] = mrr
            event_NA_df.loc[index, 'mtt'] = mtt
            event_NA_df.loc[index, 'mff'] = mff

            event_NA_df.loc[index, 'mrt'] = mrt
            event_NA_df.loc[index, 'mrf'] = mrf
            event_NA_df.loc[index, 'mtf'] = mtf

    # if mechOPT_fm then we overwrite focal_source
    if mechOPT_fm == 1:
        focal_source = "FM"
        event_NA_df.loc[index, 'strike'] = strike_fm
        event_NA_df.loc[index, 'dip'] = dip_fm
        event_NA_df.loc[index, 'rake'] = rake_fm
    print("# focal_source = ", focal_source )
    #strike, dip, rake, focal_source  = focal_info_includesuperseded(eventid)
    #event_df['strike'][i], event_df['dip'][i], event_df['rake'][i], event_df['focal_source'][i]  = focal_info(eventid)

    #print("# strile = ", strike)
    #print("# dip = ", dip)
    #print("# rake = ", rake)

    event_NA_df.loc[index, 'focal_source'] = focal_source
    

# i =  0
# index =  3
# eventid =  nn00787110
Included products: ['dyfi', 'origin', 'phase-data'] 
# returnOPT =  1
# FMOPT =  0
# mechOPT_fm =  0
# strike_fm =  -999
# dip_fm =  -999
# rake_fm =  -999
# MTOPT =  0
# mechOPT =  0
# strike =  -999
# dip =  -999
# rake =  -999
# CMTOPT =  0
# focal_source =  NA3
# i =  1
# index =  5
# eventid =  nn00787091


/Users/taira/opt/anaconda3/envs/pygmm/lib/python3.8/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


Included products: ['dyfi', 'origin', 'phase-data', 'shakemap'] 
# returnOPT =  1
# FMOPT =  0
# mechOPT_fm =  0
# strike_fm =  -999
# dip_fm =  -999
# rake_fm =  -999
# MTOPT =  0
# mechOPT =  0
# strike =  -999
# dip =  -999
# rake =  -999
# CMTOPT =  0
# focal_source =  NA3
# i =  2
# index =  8
# eventid =  nn00786813
Included products: ['dyfi', 'origin', 'phase-data'] 
# returnOPT =  1
# FMOPT =  0
# mechOPT_fm =  0
# strike_fm =  -999
# dip_fm =  -999
# rake_fm =  -999
# MTOPT =  0
# mechOPT =  0
# strike =  -999
# dip =  -999
# rake =  -999
# CMTOPT =  0
# focal_source =  NA3
# i =  3
# index =  9
# eventid =  nn00786787
Included products: ['dyfi', 'origin', 'phase-data'] 
# returnOPT =  1
# FMOPT =  0
# mechOPT_fm =  0
# strike_fm =  -999
# dip_fm =  -999
# rake_fm =  -999
# MTOPT =  0
# mechOPT =  0
# strike =  -999
# dip =  -999
# rake =  -999
# CMTOPT =  0
# focal_source =  NA3
# i =  4
# index =  11
# eventid =  nc73488761
Included products: ['dyfi', 'moment-tensor', 'nearb

In [131]:
print(event_NA_df)

                          time   latitude   longitude  depth   mag magType  \
3     2020-12-01T23:35:42.457Z  38.163800 -118.084400   4.70  3.10      ml   
5     2020-12-01T23:10:47.074Z  39.472400 -119.370800  13.10  3.80      ml   
8     2020-11-30T11:51:23.914Z  38.149700 -117.988800  10.60  3.00      ml   
9     2020-11-30T10:25:26.573Z  38.072600 -118.260700   8.00  3.00      ml   
11    2020-11-29T15:46:52.440Z  40.279000 -124.413667  20.23  3.53      mw   
...                        ...        ...         ...    ...   ...     ...   
2101  2018-03-09T06:01:28.350Z  40.291833 -124.542333  15.09  4.48      mw   
2116  2018-02-03T03:12:46.560Z  40.801000 -125.445500  13.29  4.33      mw   
2119  2018-01-27T12:40:13.570Z  40.380900 -126.311500  10.00  3.30      ml   
2120  2018-01-25T18:26:50.680Z  40.382400 -126.470000  10.74  3.30      ml   
2128  2018-01-07T19:01:00.490Z  40.398667 -125.244667  29.45  4.52      mw   

       nst     gap     dmin     rms  ...  rake focal_source Rup

In [135]:
event_noNA_df = event_df[ (event_df['focal_source']  != "NA2" ) &  (event_df['focal_source'] != "NA")  ]
print(event_noNA_df)

                          time   latitude   longitude  depth   mag magType  \
0     2020-12-01T23:47:05.591Z  38.167500 -118.081300   5.60  4.30      ml   
1     2020-12-01T23:43:08.516Z  38.172700 -118.070300   4.80  4.30      ml   
4     2020-12-01T23:32:56.573Z  38.163700 -118.083700   5.00  5.10      ml   
6     2020-12-01T04:15:12.630Z  38.050833 -118.752333   8.11  3.06      ml   
7     2020-12-01T01:54:49.480Z  35.650833 -117.467667   8.57  3.20      ml   
...                        ...        ...         ...    ...   ...     ...   
2126  2018-01-16T20:17:10.580Z  37.510000 -118.854333   9.00  3.09      ml   
2127  2018-01-11T00:15:13.680Z  36.156333 -120.229833  11.36  3.14      ml   
2129  2018-01-07T01:31:11.150Z  34.420000 -120.001500   2.26  3.78      mw   
2130  2018-01-04T10:39:37.730Z  37.855167 -122.256833  12.31  4.38      mw   
2131  2017-12-31T19:49:06.270Z  40.484667 -123.390000  30.44  3.76      mw   

        nst     gap      dmin     rms  ... magNst    status loc

## save all outpout
noNA includs all rupture and mech
NA and NA2 need to do FMC.py for mech and CMT solution

In [136]:
event_noNA_df.to_csv("event_noNA_df.csv")

In [137]:
event_NA_df.to_csv("event_NA_df.csv")

In [138]:
event_NA2_df.to_csv("event_NA2_df.csv")

In [143]:
# if FM there we use FM although MT solution may be better.
event_NA_df_mech = event_NA_df[ (event_NA_df['focal_source'] == "FM" ) | (event_NA_df['focal_source'] == "MT" )]
print(event_NA_df_mech)


                          time   latitude   longitude  depth   mag magType  \
134   2020-07-24T07:05:13.560Z  36.445167 -117.959500   7.59  3.73      mw   
176   2020-06-25T22:21:44.100Z  36.443833 -117.974833   5.43  3.12      ml   
346   2020-05-22T13:58:05.930Z  37.083167 -119.268833  44.62  3.16      ml   
514   2020-05-15T21:47:23.890Z  39.962167 -120.851000  11.71  3.07      ml   
659   2020-03-11T01:17:16.090Z  39.475167 -120.245500   7.87  3.71      mw   
...                        ...        ...         ...    ...   ...     ...   
1970  2019-03-29T04:55:25.890Z  40.428833 -124.465500  27.80  4.19      mw   
1974  2019-03-20T12:06:02.360Z  36.068000 -117.685333   0.19  3.20      ml   
2054  2018-08-17T19:25:33.730Z  40.678833 -124.897500  23.60  3.35      ml   
2062  2018-07-25T05:06:06.740Z  40.385167 -125.052333  10.59  4.53      mw   
2097  2018-03-23T03:09:39.100Z  40.427833 -124.510833  25.19  4.66      mw   

       nst    gap     dmin   rms  ...    rake focal_source Rupt

In [145]:
# if FM there we use FM although MT solution may be better.
event_NA2_df_mech = event_NA2_df[ (event_NA2_df['focal_source'] == "FM" ) | (event_NA2_df['focal_source'] == "MT" )]
print(event_NA2_df_mech)

                        time   latitude   longitude  depth   mag magType  \
16  2020-11-20T10:10:05.966Z  38.174600 -117.801500   7.40  4.00      ml   
17  2020-11-19T18:22:23.790Z  35.081000 -118.826833   2.71  3.06      ml   
20  2020-11-16T04:43:08.432Z  38.189400 -117.748200  10.60  3.60      ml   
41  2020-11-04T00:20:24.770Z  37.639167 -119.389833  11.81  3.40      ml   

     nst    gap     dmin     rms  ... magNst    status locationSource  \
16  31.0  54.57  0.05600  0.1356  ...   14.0  reviewed             nn   
17  45.0  59.00  0.04587  0.1600  ...  132.0  reviewed             ci   
20  37.0  58.02  0.03800  0.1490  ...   18.0  reviewed             nn   
41  36.0  72.00  0.24660  0.0600  ...   90.0  reviewed             nc   

   magSource  strike    dip    rake  focal_source  Rupture_type mechanism  
16        nn  174.39  57.76  171.68            MT             U         U  
17        ci   250.0   20.0     4.0            FM             U         U  
20        nn       6     

In [170]:
#df_concat_multi = pd.concat([df1, df2, df1])
# combine NA and NA2
event_redo_df_mech = pd.concat([ event_NA_df_mech, event_NA2_df_mech])
print(event_redo_df_mech)

                          time   latitude   longitude  depth   mag magType  \
134   2020-07-24T07:05:13.560Z  36.445167 -117.959500   7.59  3.73      mw   
176   2020-06-25T22:21:44.100Z  36.443833 -117.974833   5.43  3.12      ml   
346   2020-05-22T13:58:05.930Z  37.083167 -119.268833  44.62  3.16      ml   
514   2020-05-15T21:47:23.890Z  39.962167 -120.851000  11.71  3.07      ml   
659   2020-03-11T01:17:16.090Z  39.475167 -120.245500   7.87  3.71      mw   
...                        ...        ...         ...    ...   ...     ...   
2097  2018-03-23T03:09:39.100Z  40.427833 -124.510833  25.19  4.66      mw   
16    2020-11-20T10:10:05.966Z  38.174600 -117.801500   7.40  4.00      ml   
17    2020-11-19T18:22:23.790Z  35.081000 -118.826833   2.71  3.06      ml   
20    2020-11-16T04:43:08.432Z  38.189400 -117.748200  10.60  3.60      ml   
41    2020-11-04T00:20:24.770Z  37.639167 -119.389833  11.81  3.40      ml   

       nst     gap     dmin     rms  ...    rake focal_source R

In [171]:
#event_redo_df_mech['Rupture_type'] , event_redo_df_mech['mechanism'] = mechanism_info(event_redo_df_mech['strike'],  event_redo_df_mech['dip'], event_redo_df_mech['rake'], event_redo_df_mech['longitude'], event_redo_df_mech['latitude'],  event_redo_df_mech['depth'],  event_redo_df_mech['mag'],  event_redo_df_mech['id'])
#for eventid in event_df['id']:
scalarOPT = 1 # do each case. 
for i, index in enumerate(event_redo_df_mech['id'].index):
#for i, index in enumerate(event_NA_df['id'].index):

    print("# i = ",i)
    print("# index = ", index)
    eventid=event_redo_df_mech['id'][index]
    #eventid=event_NA_df['id'][index]
    print("# eventid = ", eventid)
    RupOUT , mechOUT = mechanism_info(event_redo_df_mech['strike'][index],  event_redo_df_mech['dip'][index], event_redo_df_mech['rake'][index], event_redo_df_mech['longitude'][index], event_redo_df_mech['latitude'][index],  event_redo_df_mech['depth'][index],  event_redo_df_mech['mag'][index],  event_redo_df_mech['id'][index], scalarOPT)
    print("# RupOUT = ", RupOUT)
    print("# mechOUT = ", mechOUT)
    event_redo_df_mech.loc[index, 'Rupture_type'] = RupOUT[0]
    event_redo_df_mech.loc[index, 'mechanism'] = mechOUT[0]
    
    

# i =  0
# index =  134
# eventid =  ci38605954
# evlo -117.9595
# Rupture_type =  0    SS-N
Name: Rupture_type, dtype: object
# mechanism =  0    SS
Name: mechanism, dtype: object
# RupOUT =  0    SS-N
Name: Rupture_type, dtype: object
# mechOUT =  0    SS
Name: mechanism, dtype: object
# i =  1
# index =  176
# eventid =  ci39266607
# evlo -117.9748333
# Rupture_type =  0    N
Name: Rupture_type, dtype: object
# mechanism =  0    NS
Name: mechanism, dtype: object
# RupOUT =  0    N
Name: Rupture_type, dtype: object
# mechOUT =  0    NS
Name: mechanism, dtype: object
# i =  2
# index =  346
# eventid =  nc73393256
# evlo -119.2688333
# Rupture_type =  0    R
Name: Rupture_type, dtype: object
# mechanism =  0    RS
Name: mechanism, dtype: object
# RupOUT =  0    R
Name: Rupture_type, dtype: object
# mechOUT =  0    RS
Name: mechanism, dtype: object
# i =  3
# index =  514
# eventid =  nc73386685
# evlo -120.851
# Rupture_type =  0    SS
Name: Rupture_type, dtype: object
# mechanism =  

In [172]:
len(event_redo_df_mech.index)

384

In [173]:
print(event_redo_df_mech)

                          time   latitude   longitude  depth   mag magType  \
134   2020-07-24T07:05:13.560Z  36.445167 -117.959500   7.59  3.73      mw   
176   2020-06-25T22:21:44.100Z  36.443833 -117.974833   5.43  3.12      ml   
346   2020-05-22T13:58:05.930Z  37.083167 -119.268833  44.62  3.16      ml   
514   2020-05-15T21:47:23.890Z  39.962167 -120.851000  11.71  3.07      ml   
659   2020-03-11T01:17:16.090Z  39.475167 -120.245500   7.87  3.71      mw   
...                        ...        ...         ...    ...   ...     ...   
2097  2018-03-23T03:09:39.100Z  40.427833 -124.510833  25.19  4.66      mw   
16    2020-11-20T10:10:05.966Z  38.174600 -117.801500   7.40  4.00      ml   
17    2020-11-19T18:22:23.790Z  35.081000 -118.826833   2.71  3.06      ml   
20    2020-11-16T04:43:08.432Z  38.189400 -117.748200  10.60  3.60      ml   
41    2020-11-04T00:20:24.770Z  37.639167 -119.389833  11.81  3.40      ml   

       nst     gap     dmin     rms  ...    rake focal_source R

In [176]:
# should be none
event_redo_df_mech [ event_redo_df_mech['focal_source'] == 'U']

Empty DataFrame
Columns: [time, latitude, longitude, depth, mag, magType, nst, gap, dmin, rms, net, id, updated, place, type, horizontalError, depthError, magError, magNst, status, locationSource, magSource, strike, dip, rake, focal_source, Rupture_type, mechanism, mrr, mtt, mff, mrt, mrf, mtf]
Index: []

[0 rows x 34 columns]

In [149]:
# no mech
event_NA_df_NA3 = event_NA_df[ (event_NA_df['focal_source'] == "NA3" )]
print(event_NA_df_NA3)


                          time   latitude   longitude  depth   mag magType  \
3     2020-12-01T23:35:42.457Z  38.163800 -118.084400   4.70  3.10      ml   
5     2020-12-01T23:10:47.074Z  39.472400 -119.370800  13.10  3.80      ml   
8     2020-11-30T11:51:23.914Z  38.149700 -117.988800  10.60  3.00      ml   
9     2020-11-30T10:25:26.573Z  38.072600 -118.260700   8.00  3.00      ml   
13    2020-11-24T09:23:59.347Z  38.172800 -117.821900   6.30  3.00      ml   
...                        ...        ...         ...    ...   ...     ...   
2078  2018-05-14T08:15:54.580Z  41.663666 -124.857666  13.47  3.20      ml   
2082  2018-05-06T16:29:23.960Z  40.595000 -125.092167  18.43  3.18      ml   
2091  2018-04-07T13:50:15.160Z  40.283833 -124.991000  11.16  3.28      ml   
2119  2018-01-27T12:40:13.570Z  40.380900 -126.311500  10.00  3.30      ml   
2120  2018-01-25T18:26:50.680Z  40.382400 -126.470000  10.74  3.30      ml   

       nst     gap    dmin     rms  ...  rake focal_source Rupt

In [151]:
# no mech
event_NA2_df_NA3 = event_NA2_df[ (event_NA2_df['focal_source'] == "NA3" )]
print(event_NA2_df_NA3)


                        time  latitude  longitude  depth  mag magType   nst  \
2   2020-12-01T23:39:55.064Z   38.1722  -118.0504    8.0  3.2      ml  28.0   
15  2020-11-22T01:35:02.172Z   38.1759  -117.8895   10.5  3.8      ml  32.0   
18  2020-11-16T13:52:23.067Z   38.1873  -117.7507   10.8  3.2      ml  33.0   
22  2020-11-14T15:07:33.127Z   38.1849  -117.7505   10.7  3.0      ml  26.0   
23  2020-11-14T12:42:37.140Z   38.1626  -117.8673    5.2  3.4      ml  29.0   
30  2020-11-13T11:32:48.171Z   38.1894  -117.7536   10.5  3.1      ml  30.0   
47  2020-10-27T05:45:59.765Z   38.1833  -117.8677    9.9  3.1      ml  32.0   

      gap   dmin     rms  ... magNst    status locationSource magSource  \
2   42.51  0.013  0.1349  ...   13.0  reviewed             nn        nn   
15  40.51  0.020  0.1368  ...   16.0  reviewed             nn        nn   
18  57.96  0.040  0.1599  ...   16.0  reviewed             nn        nn   
22  70.39  0.043  0.1489  ...   12.0  reviewed             nn      

In [155]:
# combine NA3 NA and NA2
event_redo_df_NA3 = pd.concat([ event_NA_df_NA3, event_NA2_df_NA3])
print(event_redo_df_NA3)

                        time  latitude  longitude  depth  mag magType   nst  \
3   2020-12-01T23:35:42.457Z   38.1638  -118.0844    4.7  3.1      ml  24.0   
5   2020-12-01T23:10:47.074Z   39.4724  -119.3708   13.1  3.8      ml  26.0   
8   2020-11-30T11:51:23.914Z   38.1497  -117.9888   10.6  3.0      ml  31.0   
9   2020-11-30T10:25:26.573Z   38.0726  -118.2607    8.0  3.0      ml  34.0   
13  2020-11-24T09:23:59.347Z   38.1728  -117.8219    6.3  3.0      ml  26.0   
..                       ...       ...        ...    ...  ...     ...   ...   
18  2020-11-16T13:52:23.067Z   38.1873  -117.7507   10.8  3.2      ml  33.0   
22  2020-11-14T15:07:33.127Z   38.1849  -117.7505   10.7  3.0      ml  26.0   
23  2020-11-14T12:42:37.140Z   38.1626  -117.8673    5.2  3.4      ml  29.0   
30  2020-11-13T11:32:48.171Z   38.1894  -117.7536   10.5  3.1      ml  30.0   
47  2020-10-27T05:45:59.765Z   38.1833  -117.8677    9.9  3.1      ml  32.0   

      gap   dmin     rms  ...  rake focal_source Ru

In [152]:
# CMT
event_NA_df_CMT = event_NA_df[ (event_NA_df['focal_source'] == "CMT" )]
print(event_NA_df_CMT)

                          time   latitude   longitude  depth   mag magType  \
11    2020-11-29T15:46:52.440Z  40.279000 -124.413667  20.23  3.53      mw   
190   2020-06-24T17:40:49.240Z  36.446833 -117.975167   4.66  5.80      mw   
395   2020-05-19T15:58:31.620Z  40.453833 -124.562000  23.64  4.17      mw   
609   2020-04-19T01:10:47.070Z  40.364333 -125.382667  21.73  3.73      mw   
654   2020-03-18T22:08:20.920Z  40.347500 -124.456167  28.61  5.21      mw   
661   2020-03-09T11:14:54.770Z  40.586667 -125.140333  24.27  3.56      mw   
662   2020-03-09T11:04:45.940Z  40.571000 -125.002833   5.63  3.68      mw   
663   2020-03-09T06:32:59.890Z  40.364833 -125.143167   7.20  4.94      mw   
664   2020-03-09T02:59:08.860Z  40.391667 -125.093667   3.19  5.77      mw   
676   2020-02-22T19:14:27.580Z  40.289500 -124.673667   7.07  4.33      mw   
685   2020-02-06T08:20:24.620Z  40.302500 -124.383500   8.80  3.76      mw   
851   2019-07-31T12:26:16.180Z  40.340667 -124.425667  27.39  3.

In [153]:
# CMT
event_NA2_df_CMT = event_NA2_df[ (event_NA2_df['focal_source'] == "CMT" )]
print(event_NA2_df_CMT)

Empty DataFrame
Columns: [time, latitude, longitude, depth, mag, magType, nst, gap, dmin, rms, net, id, updated, place, type, horizontalError, depthError, magError, magNst, status, locationSource, magSource, strike, dip, rake, focal_source, Rupture_type, mechanism]
Index: []

[0 rows x 28 columns]


In [154]:
# combine CMT NA and NA2
event_redo_df_CMT = pd.concat([ event_NA_df_CMT, event_NA2_df_CMT])
print(event_redo_df_CMT)

                          time   latitude   longitude  depth   mag magType  \
11    2020-11-29T15:46:52.440Z  40.279000 -124.413667  20.23  3.53      mw   
190   2020-06-24T17:40:49.240Z  36.446833 -117.975167   4.66  5.80      mw   
395   2020-05-19T15:58:31.620Z  40.453833 -124.562000  23.64  4.17      mw   
609   2020-04-19T01:10:47.070Z  40.364333 -125.382667  21.73  3.73      mw   
654   2020-03-18T22:08:20.920Z  40.347500 -124.456167  28.61  5.21      mw   
661   2020-03-09T11:14:54.770Z  40.586667 -125.140333  24.27  3.56      mw   
662   2020-03-09T11:04:45.940Z  40.571000 -125.002833   5.63  3.68      mw   
663   2020-03-09T06:32:59.890Z  40.364833 -125.143167   7.20  4.94      mw   
664   2020-03-09T02:59:08.860Z  40.391667 -125.093667   3.19  5.77      mw   
676   2020-02-22T19:14:27.580Z  40.289500 -124.673667   7.07  4.33      mw   
685   2020-02-06T08:20:24.620Z  40.302500 -124.383500   8.80  3.76      mw   
851   2019-07-31T12:26:16.180Z  40.340667 -124.425667  27.39  3.

In [182]:
scalarOPT = 1 # do each case. 
for i, index in enumerate(event_redo_df_CMT['id'].index):
#for i, index in enumerate(event_NA_df['id'].index):

    print("# i = ",i)
    print("# index = ", index)
    eventid=event_redo_df_CMT['id'][index]
    #eventid=event_NA_df['id'][index]
    print("# eventid = ", eventid)
    RupOUT , mechOUT = mechanism_info_fromCMT(event_redo_df_CMT['mrr'][index], event_redo_df_CMT['mtt'][index], event_redo_df_CMT['mff'][index], event_redo_df_CMT['mrt'][index], event_redo_df_CMT['mrf'][index], event_redo_df_CMT['mtf'][index], event_redo_df_CMT['longitude'][index], event_redo_df_CMT['latitude'][index],  event_redo_df_CMT['depth'][index],  event_redo_df_CMT['mag'][index],  event_redo_df_CMT['id'][index], scalarOPT)
    #mechanism_info_fromCMT(mrr, mtt, mff, mrt, mrf, mtf, evlo, evla, evdp_km, evmag, eventid, scalarOPT=1)
    print("# RupOUT = ", RupOUT)
    print("# mechOUT = ", mechOUT)
    event_redo_df_CMT.loc[index, 'Rupture_type'] = RupOUT[0]
    event_redo_df_CMT.loc[index, 'mechanism'] = mechOUT[0]
    

# i =  0
# index =  11
# eventid =  nc73488761
# evlo -124.4136667
# Rupture_type =  0    SS
Name: Rupture_type, dtype: object
# mechanism =  0    SS
Name: mechanism, dtype: object
# RupOUT =  0    SS
Name: Rupture_type, dtype: object
# mechOUT =  0    SS
Name: mechanism, dtype: object
# i =  1
# index =  190
# eventid =  ci39493944
# evlo -117.9751667
# Rupture_type =  0    N-SS
Name: Rupture_type, dtype: object
# mechanism =  0    NS
Name: mechanism, dtype: object
# RupOUT =  0    N-SS
Name: Rupture_type, dtype: object
# mechOUT =  0    NS
Name: mechanism, dtype: object
# i =  2
# index =  395
# eventid =  nc73390316
# evlo -124.562
# Rupture_type =  0    SS
Name: Rupture_type, dtype: object
# mechanism =  0    SS
Name: mechanism, dtype: object
# RupOUT =  0    SS
Name: Rupture_type, dtype: object
# mechOUT =  0    SS
Name: mechanism, dtype: object
# i =  3
# index =  609
# eventid =  nc73372865
# evlo -125.3826667
# Rupture_type =  0    SS
Name: Rupture_type, dtype: object
# mechani

In [183]:
# should be none
event_redo_df_CMT [ event_redo_df_CMT['focal_source'] == 'U']

Empty DataFrame
Columns: [time, latitude, longitude, depth, mag, magType, nst, gap, dmin, rms, net, id, updated, place, type, horizontalError, depthError, magError, magNst, status, locationSource, magSource, strike, dip, rake, focal_source, Rupture_type, mechanism, mrr, mtt, mff, mrt, mrf, mtf]
Index: []

[0 rows x 34 columns]

## combine together 
noNA + redo_df_mech + redo_df_CMT redo NA

In [185]:
event_redo_df_all = pd.concat([event_noNA_df, event_redo_df_mech,  event_redo_df_CMT, event_redo_df_NA3])
print(event_redo_df_all)

                        time   latitude   longitude  depth   mag magType  \
0   2020-12-01T23:47:05.591Z  38.167500 -118.081300   5.60  4.30      ml   
1   2020-12-01T23:43:08.516Z  38.172700 -118.070300   4.80  4.30      ml   
4   2020-12-01T23:32:56.573Z  38.163700 -118.083700   5.00  5.10      ml   
6   2020-12-01T04:15:12.630Z  38.050833 -118.752333   8.11  3.06      ml   
7   2020-12-01T01:54:49.480Z  35.650833 -117.467667   8.57  3.20      ml   
..                       ...        ...         ...    ...   ...     ...   
18  2020-11-16T13:52:23.067Z  38.187300 -117.750700  10.80  3.20      ml   
22  2020-11-14T15:07:33.127Z  38.184900 -117.750500  10.70  3.00      ml   
23  2020-11-14T12:42:37.140Z  38.162600 -117.867300   5.20  3.40      ml   
30  2020-11-13T11:32:48.171Z  38.189400 -117.753600  10.50  3.10      ml   
47  2020-10-27T05:45:59.765Z  38.183300 -117.867700   9.90  3.10      ml   

     nst    gap     dmin     rms  ...     rake focal_source Rupture_type  \
0   34.0  4

In [187]:
event_redo_df_all.index

Int64Index([   0,    1,    4,    6,    7,   10,   12,   19,   24,   35,
            ...
            2091, 2119, 2120,    2,   15,   18,   22,   23,   30,   47],
           dtype='int64', length=2132)

In [190]:
#df_s = df.sort_values(['state', 'age'])
event_redo_df_all_sort = event_redo_df_all.sort_index()
print(event_redo_df_all_sort)

                          time   latitude   longitude  depth   mag magType  \
0     2020-12-01T23:47:05.591Z  38.167500 -118.081300   5.60  4.30      ml   
1     2020-12-01T23:43:08.516Z  38.172700 -118.070300   4.80  4.30      ml   
2     2020-12-01T23:39:55.064Z  38.172200 -118.050400   8.00  3.20      ml   
3     2020-12-01T23:35:42.457Z  38.163800 -118.084400   4.70  3.10      ml   
4     2020-12-01T23:32:56.573Z  38.163700 -118.083700   5.00  5.10      ml   
...                        ...        ...         ...    ...   ...     ...   
2127  2018-01-11T00:15:13.680Z  36.156333 -120.229833  11.36  3.14      ml   
2128  2018-01-07T19:01:00.490Z  40.398667 -125.244667  29.45  4.52      mw   
2129  2018-01-07T01:31:11.150Z  34.420000 -120.001500   2.26  3.78      mw   
2130  2018-01-04T10:39:37.730Z  37.855167 -122.256833  12.31  4.38      mw   
2131  2017-12-31T19:49:06.270Z  40.484667 -123.390000  30.44  3.76      mw   

        nst     gap      dmin     rms  ...     rake focal_sourc

In [73]:

event_focal_fi = "bayarea_center_m3_500km_focal.csv"
event_focal_fi = "test_eq_focal.csv" # two events only


#focal_df = pd.DataFrame({ 'lon' : evlo})
#    focal_df = pd.DataFrame({ 'lon' : evlo,
#                            'lat' : evla,
#                            'dep' : evdp_km,
#                            'strike' : strike,
#                            'dip' : dip,
#                            'rake' : rake,
#                            'mag' : evmag,
#                            'evid' : eventid }, index=[0])

#time,latitude,longitude,depth,mag,magType,nst,gap,dmin,rms,net,id,updated,place,type,horizontalError,depthError,magError,magNst,status,locationSource,magSource

                               
event_focal_df = pd.DataFrame({ 'time' : event_df['time'],
                        'latitude' : event_df['latitude'],
                        'longitude' :event_df['longitude'],
                        'depth' : event_df['depth'],
                        'mag' : event_df['mag'],
                        'magType' : event_df['magType'],
                        'Rupture_type' : event_df['Rupture_type'], 
                        'mechanism' : event_df['mechanism'], 
                        'strike' : event_df['strike'],
                        'dip' : event_df['dip'],
                        'rake' : event_df['rake'],
                        'focal_source' : event_df['focal_source'],
                        'id' : event_df['id'] }  )

event_focal_df.to_csv(event_focal_fi, columns=['time','latitude','longitude','depth','mag','magType','id','Rupture_type','mechanism','strike','dip','rake','focal_source'], index=False, sep=',')


In [191]:
event_focal_fi_redo = "bayarea_center_m3_500km_focal_redo.csv"


event_focal_df_redo = pd.DataFrame({ 'time' : event_redo_df_all_sort['time'],
                        'latitude' : event_redo_df_all_sort['latitude'],
                        'longitude' :event_redo_df_all_sort['longitude'],
                        'depth' : event_redo_df_all_sort['depth'],
                        'mag' : event_redo_df_all_sort['mag'],
                        'magType' : event_redo_df_all_sort['magType'],
                        'Rupture_type' : event_redo_df_all_sort['Rupture_type'], 
                        'mechanism' : event_redo_df_all_sort['mechanism'], 
                        'strike' : event_redo_df_all_sort['strike'],
                        'dip' : event_redo_df_all_sort['dip'],
                        'rake' : event_redo_df_all_sort['rake'],
                        'focal_source' : event_redo_df_all_sort['focal_source'],
                        'id' : event_redo_df_all_sort['id'] }  )

event_focal_df_redo.to_csv(event_focal_fi_redo, columns=['time','latitude','longitude','depth','mag','magType','id','Rupture_type','mechanism','strike','dip','rake','focal_source'], index=False, sep=',')
